In [1]:
from ete3 import PhyloTree
from ete3 import Tree,TreeStyle,NodeStyle
import pandas as pd
import os
import re
import numpy as np
import string
from ete3 import Tree, random_color,faces, TreeStyle, NodeStyle
from ete3 import ClusterTree, CircleFace ,RectFace, AttrFace, ProfileFace, TextFace, BarChartFace,StackedBarFace
from ete3.treeview.faces import add_face_to_node
import colorsys
import random
from pathlib import Path

In [2]:
# Genreate a color randomly
def randomcolor():
    colorArr = ['1','2','3','4','5','6','7','8','9','A','B','C','D','E','F']
    color = ""
    for i in range(6):
        color += colorArr[random.randint(0,14)]
    return "#"+color

In [3]:
taxonomy = pd.read_table("/scale03/fs0/gpfs0/research/dsi-find/mlk442/correlation_table/taxonomy.txt", sep = "\t")
taxonomy.head(10)

MaterialLabel MGx Selected          Genus       species    ID
0    DA002F0001           NO   Streptomyces         albus   NaN
1    DA003H0001           NO   Streptomyces      anulatus   NaN
2    DA004A0004          YES   Streptomyces            sp  rpoB
3    DA004C0003           NO   Streptomyces            sp   NaN
4    DA004E0001          YES  Amycolatopsis      japonica  rpoB
5    DA006D0002           NO   Streptomyces            sp   NaN
6    DA006D0003           NO   Streptomyces            sp   NaN
7    DA007H0001           NO   Streptomyces            sp   NaN
8    DA007L0001           NO        Klenkia  brasiliensis   NaN
9    DA007M0001           NO   Streptomyces            sp   NaN

In [4]:
import plotly.express as px
df_taxon = taxonomy[taxonomy['MGx Selected'] == 'YES']
fig = px.sunburst(df_taxon, path=['Genus', 'species'])
fig.show()

In [5]:
taxonomy[taxonomy['MaterialLabel'] == "DA977Z0936"]

MaterialLabel MGx Selected Genus species   ID
761    DA977Z0936           NO   NaN     NaN  NaN

In [6]:
strainName = taxonomy.MaterialLabel+ " "+taxonomy.Genus +" "+ taxonomy.species
GenusSpecies = df_taxon.Genus
dict_strain = dict(zip(taxonomy.MaterialLabel.tolist(), strainName))
dict_strain["Escherichia"] = "Escherichia Escherichia coli"
len(dict_strain)

839

In [7]:
#Creat color map for each 
GenusSpeciesUniq = GenusSpecies.unique().tolist()
dict_color= {} 
for i in range(len(GenusSpeciesUniq)):
    dict_color[GenusSpeciesUniq[i]] = random_color(seed=2*i)   
dict_color["Escherichia"] = random_color(seed=len(GenusSpeciesUniq)+1 )    
len(set(dict_color.values())) == len(dict_color.keys())
dict_color

{'Streptomyces': '#bf423f',
 'Amycolatopsis': '#bf5a3f',
 'Saccharopolyspora': '#bf463f',
 'Nonomuraea': '#bf423f',
 'Actinosynnema': '#bf463f',
 'Actinomadura': '#bf423f',
 'Actinobacteria': '#bf423f',
 'Escherichia': '#bf463f'}

In [8]:
# Read the tree
with open('/home/mlk442/FIND/mlk442/phylogenetic/ropB_tree_ecoli.txt') as f:
    tree = f.readline()
t = PhyloTree(tree)
#print (t)
#tree

In [9]:
strains = list()
dict_nodeName = dict()
#dict_nodeColor = dict()
for leaf in t.iter_leaves():
    info = leaf.name.split("_")
    if (len(info) > 1):
        strain = info[1]
    else:
        strain = info[0]
        print (leaf.name)
    if strain in dict_strain.keys():
        dict_nodeName[leaf.name] = dict_strain[strain]  
        info = dict_strain[strain].split( )[1] 
        #dict_nodeColor[leaf.name] = dict_color[info]
    strains.append(strain)
dict_nodeName

Escherichia


{'P005E10_DA977Z0821': 'DA977Z0821 Streptomyces parvulus',
 'P005E07_DA977Z0824': 'DA977Z0824 Streptomyces parvulus',
 'P005E09_DA977Z0822': 'DA977Z0822 Streptomyces parvulus',
 'P005E08_DA977Z0823': 'DA977Z0823 Streptomyces parvulus',
 'P005E12_DA977Z0819': 'DA977Z0819 Streptomyces parvulus',
 'P005E11_DA977Z0820': 'DA977Z0820 Streptomyces parvulus',
 'P005B10_DA977Z0837': 'DA977Z0837 Streptomyces parvulus',
 'P007E03_DA977Z0567': 'DA977Z0567 Streptomyces parvulus',
 'P006A09_DA977Z0643': 'DA977Z0643 Streptomyces parvulus',
 'P005F01_DA977Z0818': 'DA977Z0818 Streptomyces parvulus',
 'P007G06_DA977Z0973': 'DA977Z0973 Streptomyces parvulus',
 'P004G07_DA530O0001': 'DA530O0001 Streptomyces toyocaensis',
 'P003C02_DA977Z0802': 'DA977Z0802 Streptomyces toyocaensis',
 'P006E06_DA977Z0574': 'DA977Z0574 Streptomyces toyocaensis',
 'P006E04_DA977Z0468': 'DA977Z0468 Streptomyces sp',
 'P003H06_DA977Z1000': 'DA977Z1000 Streptomyces sp',
 'P003H07_DA977Z0999': 'DA977Z0999 Streptomyces sp',
 'P011

In [10]:
for key in dict_nodeName.keys():
    tree = tree.replace(key,dict_nodeName[key])

In [11]:
t = PhyloTree(tree)
dict_nodeColor = dict()
for leaf in t.iter_leaves():
    Genus_type =leaf.name.split( )
    if (len(Genus_type) > 1):
        Genus_type = Genus_type[1]
    else:
        Genus_type = Genus_type[0]
    dict_nodeColor[leaf.name] = dict_color[Genus_type]
    
set(list(dict_nodeColor.values()))

{'#bf423f', '#bf463f', '#bf5a3f'}

In [12]:
Genus_type

'Streptomyces'

In [13]:
inputDir = "/home/mlk442/FIND/mlk442/BGC_table"
os.chdir(inputDir)
count =0
gcfs = []
for strain in strains:
    cvspath =inputDir +"/" +strain+"_BGC_table.csv"
    if Path(cvspath).is_file():
        count = count+1
        strain_file = pd.read_csv(cvspath, header =1)
        gcfs.append(strain_file.GCFs.tolist())

In [14]:
flatten = lambda l: [item for sublist in l for item in sublist]

In [15]:
new_list = []
gcfs =flatten(gcfs)
for i in range(len(gcfs)):
    if isinstance(gcfs[i], str):
        new_list.append(gcfs[i].split("_")[0])

In [16]:
def list2dict(a):
    dict_gcf = {}
    for key in a:
        dict_gcf[key] = dict_gcf.get(key, 0) + 1
    return (dict_gcf)

In [17]:
col_name = list(set(new_list))
col_name.append("Strain_name")
df = pd.DataFrame(columns = col_name)
gcf = []
for strain in strains:
    cvspath =inputDir +"/" +strain+"_BGC_table.csv"
    if Path(cvspath).is_file():
        gcf_name = []
        dict_gcf = {}
        strain_file = pd.read_csv(cvspath, header =1)
        gcf = strain_file.GCFs.tolist()
        for i in range(len(gcf)):
            if isinstance(gcfs[i], str):
                gcf_name.append(gcfs[i].split("_")[0])
        dict_gcfCount = list2dict(gcf_name)
        dict_gcfCount["Strain_name"] = dict_strain[strain]
        df = df.append(dict_gcfCount,ignore_index=True)          

In [18]:
df = df.fillna(0)
df.set_index(["Strain_name"], inplace=True)

In [19]:
col_name

['NRPS',
 'Others',
 'PKSother',
 'PKSI',
 'Terpene',
 'Saccharides',
 'RiPPs',
 'Strain_name']

In [20]:
bar_color = []
for i in range(len(col_name)-1):
    bar_color.append(randomcolor())
bar_color

['#6734C1', '#234D94', '#7B1888', '#78A4FE', '#7284D1', '#C5978F', '#F7C2B5']

In [21]:
data = df
data.index.name = "#Names" 
data_mat = data.to_csv(None, sep="\t", float_format="%.2f")
header = list(data.columns.values)  
data

NRPS  Others  PKSother  PKSI  Terpene  \
#Names                                                                    
DA977Z0821 Streptomyces parvulus     6      10         2     0        5   
DA977Z0824 Streptomyces parvulus     6      11         2     0        5   
DA977Z0822 Streptomyces parvulus     7      11         2     0        5   
DA977Z0823 Streptomyces parvulus     8      13         2     0        5   
DA977Z0819 Streptomyces parvulus     6       9         2     0        4   
...                                ...     ...       ...   ...      ...   
DA977Z0774 Streptomyces sp          30      48        11     0       26   
DA977Z0794 Streptomyces sp          11      15         3     0        8   
DA977Z0796 Streptomyces sp           8      13         3     0        5   
DA977Z0829 Streptomyces sp           7      11         2     0        5   
DA977Z0838 Streptomyces parvulus     7      12         2     0        5   

                                  Saccharides  RiPPs  
#Names                                                
DA977Z0821 Streptomyces parvulus            0      4  
DA977Z0824 Streptomyces parvulus            0      4  
DA977Z0822 Streptomyces parvulus            0      4  
DA977Z0823 Streptomyces parvulus            0      4  
DA977Z0819 Streptomyces parvulus            0      4  
...                                       ...    ...  
DA977Z0774 Streptomyces sp                  0     17  
DA977Z0794 Streptomyces sp                  0      6  
DA977Z0796 Streptomyces sp                  0      4  
DA977Z0829 Streptomyces sp                  0      4  
DA977Z0838 Streptomyces parvulus            0      4  

[217 rows x 7 columns]

In [22]:
nameFace = AttrFace("name", fsize=12) #Set leaf node attribute

def setup_percentPlot(tree, tree_style, header,bar_color, nameMap ={}, nameLabel = ''):
    # Add heatmap colors to tree
    cols_add_before_heat = 0
    if nameMap:
        cols_add_before_heat = 1
    for lf in tree:
        if nameMap:
            longNameFace = faces.TextFace(nameMap.get(lf.name, lf.name))
            lf.add_face(longNameFace, column=0, position="aligned")
        new_list = []
        for i, value in enumerate(getattr(lf, "profile", [])):
            #if i != 6:
            new_list.append(value)
            
        new_list = np.array(new_list)
        lf.add_face(StackedBarFace(new_list/1.5, width = np.sum(new_list)*5 , height=20, colors=bar_color),position="aligned", column=1+cols_add_before_heat)
			# Uncomment to add numeric values to the matrix
			#lf.add_face(TextFace("%0.2f "%value, fsize=5), position="aligned", column=i)
        #lf.add_face(nameFace, column=i+cols_add_before_heat+1, position="aligned")
    #if nameMap and nameLabel:
    #    nameF = TextFace(nameLabel, fsize=7)
        #nameF.rotation = -90
    #    tree_style.aligned_header.add_face(nameF, column=0)
    # Add header 
    #for i, name in enumerate(header):
    #    nameF = TextFace(name, fsize=7)
    #    nameF.rotation = -90
    #    tree_style.aligned_header.add_face(nameF, column=i+cols_add_before_heat)

In [23]:
ts = TreeStyle()
ts.show_leaf_name = False
ts.show_branch_length = False
ts.show_branch_support = False
ts.title.add_face(TextFace("Phylogenetic tree with GCFs bar plot using ropB sequence", fsize=20), column=1)
for i in range(len(bar_color)):
    ts.legend.add_face(RectFace(20, 20,fgcolor =bar_color[i] ,bgcolor= bar_color[i] , label=None), column=4)
#ts.legend.add_face(BarChartFace(20*np.ones(len(bar_color)), deviations=None, width=200, height=100, 
#                                colors= bar_color, labels=col_name),  column=4)
#    ts.legend.add_face(CircleFace(10, bar_color[i]), column=4)
    ts.legend.add_face(TextFace(col_name[i]), column=5)
# Creates my own layout function. I will use all previously created
# faces and will set different node styles depending on the type of
# node.
                   
def mylayout(node):   
    # If node is a leaf, add the nodes name and a its scientific
    # name
    if node.is_leaf():
        # We can also create faces on the fly
        #newName = dict_nodeName.get(node.name, node.name)
        color = dict_nodeColor.get(node.name, node.name)
        #newNameFace = faces.TextFace(newName,fgcolor =color  )
        #faces.add_face_to_node(newNameFace, node, column=1, aligned=True)
        name_face = TextFace(node.name, fgcolor=color, fsize=10)
        node.add_face(name_face, column=1, position='branch-right')
        # Sets the style of leaf nodes
        node.img_style["size"] = 10
        node.img_style["shape"] = "sphere"
        node.img_style["fgcolor"] = color
    #If node is an internal node
    else:
        # Sets the style of internal nodes
        node.img_style["size"] = 2
        node.img_style["shape"] = "circle"
        node.img_style["fgcolor"] = "darkred"

#ts.layout_fn = mylayout

t.img_style["size"] = 30
t.img_style["fgcolor"] = "black"

#t.render(file_name="%%inline", w=600, tree_style=ts)
#t.show(tree_style=ts)

In [24]:
df.append(dict_gcfCount,ignore_index=True)
ts.layout_fn = mylayout
tc = ClusterTree(tree,data_mat )
setup_percentPlot(tc, ts, header,bar_color)
#t.render(file_name="treeWithplot.pdf", tree_style=ts)
#tc.render(file_name="%%inline", tree_style=ts)#%%inline

[1] leaf names could not be mapped to the matrix rows.


In [25]:
#tc.render(file_name="ropBTreeWithBarplotEcoli.pdf", w=600, tree_style=ts)
tc.render(file_name="%%inline", tree_style=ts)#%%inline

In [26]:
tc.render(file_name="treeWithplot.pdf", tree_style=ts)

{'nodes': [[0.5, 212.4566169064492, 3.5, 215.4566169064492, 0, None],
  [2.6201966854853396, 33.5, 5.62019668548534, 36.5, 1, None],
  [4.62019668548534, 12.5, 15.62019668548534, 23.5, 2, None],
  [4.62019668548534, 46.5, 15.62019668548534, 57.5, 3, None],
  [2.6201966854853254, 80.5, 13.620196685485325, 91.5, 4, None],
  [2.6201966854853396,
   391.4132338128984,
   5.62019668548534,
   394.4132338128984,
   5,
   None],
  [4.740393370970665, 114.5, 15.740393370970665, 125.5, 6, None],
  [4.740393370970679,
   664.3264676257968,
   7.740393370970679,
   667.3264676257968,
   7,
   None],
  [6.8605900564560045, 148.5, 17.860590056456005, 159.5, 8, None],
  [6.860590056456019,
   1176.1529352515936,
   9.860590056456019,
   1179.1529352515936,
   9,
   None],
  [8.980786741941344, 182.5, 19.980786741941344, 193.5, 10, None],
  [9.58614095793116,
   2165.805870503187,
   12.58614095793116,
   2168.805870503187,
   11,
   None],
  [11.699781460571852, 216.5, 22.699781460571852, 227.5, 12,

In [27]:
tc = ClusterTree(tree, percDataMartix)

NameError: name 'percDataMartix' is not defined

In [ ]:
percDataMartix

In [ ]:
nameFace = AttrFace("name", fsize=12) #Set leaf node attribute

def setup_percentPlot(tree, tree_style, header,bar_color, nameMap ={}, nameLabel = ''):
    # Add heatmap colors to tree
    cols_add_before_heat = 0
    if nameMap:
        cols_add_before_heat = 1
    for lf in tree:
        if nameMap:
            longNameFace = faces.TextFace(nameMap.get(lf.name, lf.name))
            lf.add_face(longNameFace, column=0, position="aligned")
        for i, value in enumerate(getattr(lf, "profile", [])):
            lf.add_face(RectFace(5*value, 20, bar_color[i], bar_color[i]), position="aligned", column=i+cols_add_before_heat)
			# Uncomment to add numeric values to the matrix
			#lf.add_face(TextFace("%0.2f "%value, fsize=5), position="aligned", column=i)
        #lf.add_face(nameFace, column=i+cols_add_before_heat+1, position="aligned")
    if nameMap and nameLabel:
        nameF = TextFace(nameLabel, fsize=7)
        #nameF.rotation = -90
        tree_style.aligned_header.add_face(nameF, column=0)
    # Add header 
    for i, name in enumerate(header):
        nameF = TextFace(name, fsize=7)
        nameF.rotation = -90
        tree_style.aligned_header.add_face(nameF, column=i+cols_add_before_heat)